In [1]:
from tool import get_soup

In [2]:
url = 'https://www.imdb.com/chart/moviemeter/'

In [3]:
# tool.py 未加headers不行，加了就OK了

soup=get_soup(url)    #用網頁上文字，找找看有沒有在soup裡，確認OK
soup

<!DOCTYPE html>
<html lang="en-US" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraphprotocol.org/schema/"><head><meta charset="utf-8"/><meta content="width=device-width" name="viewport"/><script>if(typeof uet === 'function'){ uet('bb', 'LoadTitle', {wb: 1}); }</script><script>window.addEventListener('load', (event) => {
        if (typeof window.csa !== 'undefined' && typeof window.csa === 'function') {
            var csaLatencyPlugin = window.csa('Content', {
                element: {
                    slotId: 'LoadTitle',
                    type: 'service-call'
                }
            });
            csaLatencyPlugin('mark', 'clickToBodyBegin', 1699805481885);
        }
    })</script><title>Most Popular Movies</title><meta content="As determined by IMDb users" data-id="main" name="description"/><meta content="IMDb" property="og:site_name"/><meta content="Most Popular Movies" property="og:title"/><meta content="As determined by IMDb users" property="o

### 目標
- 首頁：本週排名、上週排名、片名、連結
- 子頁：上映年、片長、類型、IMDb Rating、預告片連結、圖片連結

In [4]:
# 先試抓再用findall
# 結果發現是字典格式（其實是json）
# 用.text共前後的script標籤提掉
mvs = soup.find('script', id='__NEXT_DATA__').text
mvs

'{"props":{"pageProps":{"initialRefinerQueryInfo":{"queryContext":{"personalized":false,"serverSideCacheable":true},"queryVariables":{}},"pageData":{"chartTitles":{"edges":[{"currentRank":1,"node":{"id":"tt4589218","titleText":{"text":"佛萊迪餐館之五夜驚魂","__typename":"TitleText"},"titleType":{"id":"movie","text":"Movie","canHaveEpisodes":false,"displayableProperty":{"value":{"plainText":"","__typename":"Markdown"},"__typename":"DisplayableTitleTypeProperty"},"__typename":"TitleType"},"originalTitleText":{"text":"Five Nights at Freddy\'s","__typename":"TitleText"},"primaryImage":{"id":"rm2389204737","width":3158,"height":5000,"url":"https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg","caption":{"plainText":"Kevin Foster, Jess Weiss, Roger Joseph Manning Jr., and Jade Kindar-Martin in 佛萊迪餐館之五夜驚魂 (2023)","__typename":"Markdown"},"__typename":"Image"},"releaseYear":{"year":2023,"endYear":null,"__typename":"YearRange"},"rat

In [5]:
type(mvs)

str

In [6]:
# 轉做json，用dumps（注意，loads有s）
# 愛編碼

import json

# 把str轉做dict
dmvs=json.loads(mvs)


In [7]:
type(dmvs)

dict

In [8]:
# 用網頁上文字在網頁原始碼進行ctrl+f進行定位
# 發見片的連結不在dict內底，soup內底有
# 問題是soup的href那區沒放英語片名
# 看片名的構成，發現是 imdb.com/title/{id}

dmvs

{'props': {'pageProps': {'initialRefinerQueryInfo': {'queryContext': {'personalized': False,
     'serverSideCacheable': True},
    'queryVariables': {}},
   'pageData': {'chartTitles': {'edges': [{'currentRank': 1,
       'node': {'id': 'tt4589218',
        'titleText': {'text': '佛萊迪餐館之五夜驚魂', '__typename': 'TitleText'},
        'titleType': {'id': 'movie',
         'text': 'Movie',
         'canHaveEpisodes': False,
         'displayableProperty': {'value': {'plainText': '',
           '__typename': 'Markdown'},
          '__typename': 'DisplayableTitleTypeProperty'},
         '__typename': 'TitleType'},
        'originalTitleText': {'text': "Five Nights at Freddy's",
         '__typename': 'TitleText'},
        'primaryImage': {'id': 'rm2389204737',
         'width': 3158,
         'height': 5000,
         'url': 'https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg',
         'caption': {'plainText': 'Kevin Fos

In [9]:
# 試看結構

dmvs['props']['pageProps']['initialRefinerQueryInfo']['queryContext']

{'personalized': False, 'serverSideCacheable': True}

In [10]:
dmvs['props']['pageProps']

{'initialRefinerQueryInfo': {'queryContext': {'personalized': False,
   'serverSideCacheable': True},
  'queryVariables': {}},
 'pageData': {'chartTitles': {'edges': [{'currentRank': 1,
     'node': {'id': 'tt4589218',
      'titleText': {'text': '佛萊迪餐館之五夜驚魂', '__typename': 'TitleText'},
      'titleType': {'id': 'movie',
       'text': 'Movie',
       'canHaveEpisodes': False,
       'displayableProperty': {'value': {'plainText': '',
         '__typename': 'Markdown'},
        '__typename': 'DisplayableTitleTypeProperty'},
       '__typename': 'TitleType'},
      'originalTitleText': {'text': "Five Nights at Freddy's",
       '__typename': 'TitleText'},
      'primaryImage': {'id': 'rm2389204737',
       'width': 3158,
       'height': 5000,
       'url': 'https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg',
       'caption': {'plainText': 'Kevin Foster, Jess Weiss, Roger Joseph Manning Jr., and Jade Kindar-Mar

In [11]:
# 找到有關係的那層
data=dmvs['props']['pageProps']['pageData']['chartTitles']['edges']
data

[{'currentRank': 1,
  'node': {'id': 'tt4589218',
   'titleText': {'text': '佛萊迪餐館之五夜驚魂', '__typename': 'TitleText'},
   'titleType': {'id': 'movie',
    'text': 'Movie',
    'canHaveEpisodes': False,
    'displayableProperty': {'value': {'plainText': '',
      '__typename': 'Markdown'},
     '__typename': 'DisplayableTitleTypeProperty'},
    '__typename': 'TitleType'},
   'originalTitleText': {'text': "Five Nights at Freddy's",
    '__typename': 'TitleText'},
   'primaryImage': {'id': 'rm2389204737',
    'width': 3158,
    'height': 5000,
    'url': 'https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg',
    'caption': {'plainText': 'Kevin Foster, Jess Weiss, Roger Joseph Manning Jr., and Jade Kindar-Martin in 佛萊迪餐館之五夜驚魂 (2023)',
     '__typename': 'Markdown'},
    '__typename': 'Image'},
   'releaseYear': {'year': 2023, 'endYear': None, '__typename': 'YearRange'},
   'ratingsSummary': {'aggregateRating': 5.5,
   

In [12]:
# 發現是list（在dict裡面的一個list元素）

type(data)

list

In [13]:
# list裡面的每一支片都是一個字典
data[0]

{'currentRank': 1,
 'node': {'id': 'tt4589218',
  'titleText': {'text': '佛萊迪餐館之五夜驚魂', '__typename': 'TitleText'},
  'titleType': {'id': 'movie',
   'text': 'Movie',
   'canHaveEpisodes': False,
   'displayableProperty': {'value': {'plainText': '',
     '__typename': 'Markdown'},
    '__typename': 'DisplayableTitleTypeProperty'},
   '__typename': 'TitleType'},
  'originalTitleText': {'text': "Five Nights at Freddy's",
   '__typename': 'TitleText'},
  'primaryImage': {'id': 'rm2389204737',
   'width': 3158,
   'height': 5000,
   'url': 'https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg',
   'caption': {'plainText': 'Kevin Foster, Jess Weiss, Roger Joseph Manning Jr., and Jade Kindar-Martin in 佛萊迪餐館之五夜驚魂 (2023)',
    '__typename': 'Markdown'},
   '__typename': 'Image'},
  'releaseYear': {'year': 2023, 'endYear': None, '__typename': 'YearRange'},
  'ratingsSummary': {'aggregateRating': 5.5,
   'voteCount': 60793,
 

In [14]:
# 一共有幾支片

len(data)

100

In [15]:
# 發現其他東西都在node之下，要由node先進去

data[0]['node']

{'id': 'tt4589218',
 'titleText': {'text': '佛萊迪餐館之五夜驚魂', '__typename': 'TitleText'},
 'titleType': {'id': 'movie',
  'text': 'Movie',
  'canHaveEpisodes': False,
  'displayableProperty': {'value': {'plainText': '', '__typename': 'Markdown'},
   '__typename': 'DisplayableTitleTypeProperty'},
  '__typename': 'TitleType'},
 'originalTitleText': {'text': "Five Nights at Freddy's",
  '__typename': 'TitleText'},
 'primaryImage': {'id': 'rm2389204737',
  'width': 3158,
  'height': 5000,
  'url': 'https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg',
  'caption': {'plainText': 'Kevin Foster, Jess Weiss, Roger Joseph Manning Jr., and Jade Kindar-Martin in 佛萊迪餐館之五夜驚魂 (2023)',
   '__typename': 'Markdown'},
  '__typename': 'Image'},
 'releaseYear': {'year': 2023, 'endYear': None, '__typename': 'YearRange'},
 'ratingsSummary': {'aggregateRating': 5.5,
  'voteCount': 60793,
  '__typename': 'RatingsSummary'},
 'runtime': {'seco

In [16]:
# 再觀察

data[0]['node']['meterRanking']

{'currentRank': 1,
 'rankChange': {'changeDirection': 'FLAT',
  'difference': 0,
  '__typename': 'MeterRankChange'},
 '__typename': 'TitleMeterRanking'}

In [17]:
#以第一名為例
#本週排名
cRank=data[0]['currentRank']
cRank

#上週排名
if data[0]['node']['meterRanking']['rankChange']['changeDirection']=='UP':
    pRank=cRank+data[0]['node']['meterRanking']['rankChange']['difference']
elif data[0]['node']['meterRanking']['rankChange']['changeDirection']=='DOWN':
    pRank=cRank-data[0]['node']['meterRanking']['rankChange']['difference']
else:
    pRank=cRank
pRank


1

In [18]:
#片名
title = data[0]['node']['originalTitleText']['text']
title

"Five Nights at Freddy's"

In [19]:
#連結
num= data[0]['node']['id']
num

'tt4589218'

In [20]:
#連結
link = 'https://imdb.com/title/'+num
print(link)
# 試連成功

https://imdb.com/title/tt4589218


In [21]:
# 子頁：上映年、片長、類型、IMDb Rating、預告片連結、圖片連結
# 上映年、IMDb Rating、類型、圖片連結 頂懸的資料結構就有，先揣
#上映年
year = data[0]['node']['releaseYear']['year']
year


2023

In [22]:
#IMDb Rating
rating=data[0]['node']['ratingsSummary']['aggregateRating']
rating


5.5

In [23]:
#類型；本來取[2]，後來發現並不是每支電影都有[2]，改取[0]
genre=data[0]['node']['titleGenres']['genres'][0]['genre']['text']
genre


'Horror'

In [24]:
#圖片連結
pic=genre=data[0]['node']['primaryImage']['url']
print(pic)

https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg


In [25]:
# 進去各電影個別網頁找剩下的兩個資訊：片長、預告片連結

subsoup=get_soup(link)
subsoup

<!DOCTYPE html>
<html lang="en-US" xmlns:fb="http://www.facebook.com/2008/fbml" xmlns:og="http://opengraphprotocol.org/schema/"><head><meta charset="utf-8"/><meta content="width=device-width" name="viewport"/><script>if(typeof uet === 'function'){ uet('bb', 'LoadTitle', {wb: 1}); }</script><script>window.addEventListener('load', (event) => {
        if (typeof window.csa !== 'undefined' && typeof window.csa === 'function') {
            var csaLatencyPlugin = window.csa('Content', {
                element: {
                    slotId: 'LoadTitle',
                    type: 'service-call'
                }
            });
            csaLatencyPlugin('mark', 'clickToBodyBegin', 1699805549160);
        }
    })</script><title>佛萊迪餐館之五夜驚魂 (2023) - IMDb</title><meta content="佛萊迪餐館之五夜驚魂: Directed by Emma Tammi. With Josh Hutcherson, Piper Rubio, Elizabeth Lail, Matthew Lillard. A troubled security guard begins working at Freddy Fazbear's Pizza. During his first night on the job, he realize

In [26]:
# 片長
ul=subsoup.find('ul',class_='ipc-inline-list ipc-inline-list--show-dividers sc-7f1a92f5-4 kIoyyw baseAlt')
length=ul.find_all('li',class_='ipc-inline-list__item')[2].text.strip()
length

'1h 49m'

In [27]:
# 預告片連結
prem=subsoup.find_all('a',class_='ipc-lockup-overlay ipc-focusable')[1].get('href')
prem

'/video/vi889046809/?ref_=tt_vi_i_1'

In [28]:
# 預告片連結
print('https://imdb.com'+prem)

https://imdb.com/video/vi889046809/?ref_=tt_vi_i_1


In [29]:
# 準備將資料組合做一個list結構


#本週排名
cRank=data[0]['currentRank']
print(cRank)

#上週排名
if data[0]['node']['meterRanking']['rankChange']['changeDirection']=='UP':
    pRank=cRank+data[0]['node']['meterRanking']['rankChange']['difference']
elif data[0]['node']['meterRanking']['rankChange']['changeDirection']=='DOWN':
    pRank=cRank-data[0]['node']['meterRanking']['rankChange']['difference']
else:
    pRank=cRank
print(pRank)

#片名
title = data[0]['node']['originalTitleText']['text']
print(title)

#連結
num= data[0]['node']['id']
num
link = 'https://imdb.com/title/'+num
print(link)

#上映年
year = data[0]['node']['releaseYear']['year']
print(year)

#IMDb Rating
rating=data[0]['node']['ratingsSummary']['aggregateRating']
print(rating)

#類型
genre=data[0]['node']['titleGenres']['genres'][0]['genre']['text']
print(genre)

#圖片連結
pic=genre=data[0]['node']['primaryImage']['url']
print(pic)

# 片長
ul=subsoup.find('ul',class_='ipc-inline-list ipc-inline-list--show-dividers sc-7f1a92f5-4 kIoyyw baseAlt')
length=ul.find_all('li',class_='ipc-inline-list__item')[2].text.strip()
print(length)
#ul=subsoup.find('ul',class_='ipc-inline-list ipc-inline-list--show-dividers sc-afe43def-4 kdXikI baseAlt')
#length=ul.find_all('li',class_='ipc-inline-list__item')[2].text.strip()
#length

# 預告片連結
#prem=subsoup.find('a',class_='ipc-lockup-overlay ipc-focusable').get('href')
prem=subsoup.find_all('a',class_='ipc-lockup-overlay ipc-focusable')[1].get('href')
premlink = 'https://imdb.com'+prem
print(premlink)

1
1
Five Nights at Freddy's
https://imdb.com/title/tt4589218
2023
5.5
Horror
https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg
1h 49m
https://imdb.com/video/vi889046809/?ref_=tt_vi_i_1


In [30]:
# 測試以上程式碼，發現若有問題，都是在「片長」之後才出現問題，檢查結果，是「片長」該處有時沒有「分級資訊」，所以會找不到[2]，所以要用條件式判斷
# 先試片長改寫在有問題的第23名電影看可行否

subsoup=get_soup('https://www.imdb.com/title/tt15654328/?ref_=chtmvm_t_23')
ul=subsoup.find('ul',class_='ipc-inline-list ipc-inline-list--show-dividers sc-7f1a92f5-4 kIoyyw baseAlt')
leng=ul.find_all('li',class_='ipc-inline-list__item')
if len(leng)==3:
    length=leng[2].text.strip()
else:
    length=leng[1].text.strip()
print(length)

2h 44m


In [32]:
pop_movies = []

for i in range(0,100):   #

# 把原來的[0]都換成[i]；中間都print出訊息，才知道進度
# 加try, except，才不會因錯誤而中斷
    movie=[]

    try:
        print(f'現在開始抓第{i+1}名的電影...')
        
        # 本周排名
        print(f'現在開始抓第{i+1}名的目前排名！')
        cRank=data[i]['currentRank']
        movie.append(cRank)

        # 上周排名
        print(f'現在開始抓第{i+1}名之前的排名！')
        if data[i]['node']['meterRanking']['rankChange']['changeDirection']=='UP':
            pRank=cRank+data[i]['node']['meterRanking']['rankChange']['difference']
        elif data[i]['node']['meterRanking']['rankChange']['changeDirection']=='DOWN':
            pRank=cRank-data[i]['node']['meterRanking']['rankChange']['difference']
        else:
            pRank=cRank
        movie.append(pRank)

        #片名
        print(f'現在開始抓第{i+1}名的片名！')
        title = data[i]['node']['originalTitleText']['text']
        movie.append(title)

        #連結
        print(f'現在開始抓第{i+1}名的連結！')
        num= data[i]['node']['id']
        num
        link = 'https://imdb.com/title/'+num
        movie.append(link)

        # 入去囝頁的兩項用link入去，愛佇遮處理
        subsoup=get_soup(link)
        
        # 片長
        # 發現若有問題，攏是佇「片長」了後有問題，檢查結果，是「片長」彼位有時無「分級資訊」，所以會揣無[2]，愛用條件式判斷
        print(f'現在開始抓第{i+1}名的片長！')
        ul=subsoup.find('ul',class_='ipc-inline-list ipc-inline-list--show-dividers sc-7f1a92f5-4 kIoyyw baseAlt')
        leng=ul.find_all('li',class_='ipc-inline-list__item')
        if title=='The Fall Guy': #The Fall Guy沒有片長但有分級資訊
            movie.append('None')
        elif len(leng)==3:
            length=leng[2].text.strip()
            movie.append(length)
        elif len(leng)==1: #若沒有片長資料讓它顯示None
            movie.append('None')
        else:
            length=leng[1].text.strip()
            movie.append(length)

        # 預告片連結
        print(f'現在開始抓第{i+1}名的預告片連結！')
        if title=='Beetlejuice 2':
            prem=subsoup.find_all('a',class_='ipc-lockup-overlay ipc-focusable')[0].get('href')
            premlink = 'https://imdb.com'+prem
            movie.append(premlink)
        else:
            prem=subsoup.find_all('a',class_='ipc-lockup-overlay ipc-focusable')[1].get('href')
            premlink = 'https://imdb.com'+prem
            movie.append(premlink)

        #上映年
        print(f'現在開始抓第{i+1}名的發行年度！')
        year = data[i]['node']['releaseYear']['year']
        movie.append(year)

        #IMDb Rating
        print(f'現在開始抓第{i+1}名的評分！')
        rating=data[i]['node']['ratingsSummary']['aggregateRating']
        movie.append(rating)

        #類型
        print(f'現在開始抓第{i+1}名的類型！')
        genre=data[i]['node']['titleGenres']['genres'][0]['genre']['text']
        movie.append(genre)

        #圖片連結，但Beetlejuice 2沒有圖片
        print(f'現在開始抓第{i+1}名的圖片連結！')
        if title=='Beetlejuice 2':
            movie.append('None')
        else:
            pic=genre=data[i]['node']['primaryImage']['url']
            movie.append(pic)
        
        pop_movies.append(movie)
        
    except Exception as e:
        print(f'第{i+1}名有問題！',e)
        pass
pop_movies

現在開始抓第1名的電影...
現在開始抓第1名的目前排名！
現在開始抓第1名之前的排名！
現在開始抓第1名的片名！
現在開始抓第1名的連結！
現在開始抓第1名的片長！
現在開始抓第1名的預告片連結！
現在開始抓第1名的發行年度！
現在開始抓第1名的評分！
現在開始抓第1名的類型！
現在開始抓第1名的圖片連結！
現在開始抓第2名的電影...
現在開始抓第2名的目前排名！
現在開始抓第2名之前的排名！
現在開始抓第2名的片名！
現在開始抓第2名的連結！
現在開始抓第2名的片長！
現在開始抓第2名的預告片連結！
現在開始抓第2名的發行年度！
現在開始抓第2名的評分！
現在開始抓第2名的類型！
現在開始抓第2名的圖片連結！
現在開始抓第3名的電影...
現在開始抓第3名的目前排名！
現在開始抓第3名之前的排名！
現在開始抓第3名的片名！
現在開始抓第3名的連結！
現在開始抓第3名的片長！
現在開始抓第3名的預告片連結！
現在開始抓第3名的發行年度！
現在開始抓第3名的評分！
現在開始抓第3名的類型！
現在開始抓第3名的圖片連結！
現在開始抓第4名的電影...
現在開始抓第4名的目前排名！
現在開始抓第4名之前的排名！
現在開始抓第4名的片名！
現在開始抓第4名的連結！
現在開始抓第4名的片長！
現在開始抓第4名的預告片連結！
現在開始抓第4名的發行年度！
現在開始抓第4名的評分！
現在開始抓第4名的類型！
現在開始抓第4名的圖片連結！
現在開始抓第5名的電影...
現在開始抓第5名的目前排名！
現在開始抓第5名之前的排名！
現在開始抓第5名的片名！
現在開始抓第5名的連結！
現在開始抓第5名的片長！
現在開始抓第5名的預告片連結！
現在開始抓第5名的發行年度！
現在開始抓第5名的評分！
現在開始抓第5名的類型！
現在開始抓第5名的圖片連結！
現在開始抓第6名的電影...
現在開始抓第6名的目前排名！
現在開始抓第6名之前的排名！
現在開始抓第6名的片名！
現在開始抓第6名的連結！
現在開始抓第6名的片長！
現在開始抓第6名的預告片連結！
現在開始抓第6名的發行年度！
現在開始抓第6名的評分！
現在開始抓第6名的類型！
現在開始抓第6名的圖片連結！
現在開始抓第7名的電影...
現在開始抓第7名的目前排名！
現在開始抓第7名之前的排名！
現在開始抓第7名的片名！
現在開始抓第

現在開始抓第51名的片長！
現在開始抓第51名的預告片連結！
現在開始抓第51名的發行年度！
現在開始抓第51名的評分！
現在開始抓第51名的類型！
現在開始抓第51名的圖片連結！
現在開始抓第52名的電影...
現在開始抓第52名的目前排名！
現在開始抓第52名之前的排名！
現在開始抓第52名的片名！
現在開始抓第52名的連結！
現在開始抓第52名的片長！
現在開始抓第52名的預告片連結！
現在開始抓第52名的發行年度！
現在開始抓第52名的評分！
現在開始抓第52名的類型！
現在開始抓第52名的圖片連結！
現在開始抓第53名的電影...
現在開始抓第53名的目前排名！
現在開始抓第53名之前的排名！
現在開始抓第53名的片名！
現在開始抓第53名的連結！
現在開始抓第53名的片長！
現在開始抓第53名的預告片連結！
現在開始抓第53名的發行年度！
現在開始抓第53名的評分！
現在開始抓第53名的類型！
現在開始抓第53名的圖片連結！
現在開始抓第54名的電影...
現在開始抓第54名的目前排名！
現在開始抓第54名之前的排名！
現在開始抓第54名的片名！
現在開始抓第54名的連結！
現在開始抓第54名的片長！
現在開始抓第54名的預告片連結！
現在開始抓第54名的發行年度！
現在開始抓第54名的評分！
現在開始抓第54名的類型！
現在開始抓第54名的圖片連結！
現在開始抓第55名的電影...
現在開始抓第55名的目前排名！
現在開始抓第55名之前的排名！
現在開始抓第55名的片名！
現在開始抓第55名的連結！
現在開始抓第55名的片長！
現在開始抓第55名的預告片連結！
現在開始抓第55名的發行年度！
現在開始抓第55名的評分！
現在開始抓第55名的類型！
現在開始抓第55名的圖片連結！
現在開始抓第56名的電影...
現在開始抓第56名的目前排名！
現在開始抓第56名之前的排名！
現在開始抓第56名的片名！
現在開始抓第56名的連結！
現在開始抓第56名的片長！
現在開始抓第56名的預告片連結！
現在開始抓第56名的發行年度！
現在開始抓第56名的評分！
現在開始抓第56名的類型！
現在開始抓第56名的圖片連結！
現在開始抓第57名的電影...
現在開始抓第57名的目前排名！
現在開始抓第57名之前的排名！
現在開始抓第57名的片名！
現在開始抓第57名的連結

[[1,
  1,
  "Five Nights at Freddy's",
  'https://imdb.com/title/tt4589218',
  '1h 49m',
  'https://imdb.com/video/vi889046809/?ref_=tt_vi_i_1',
  2023,
  5.5,
  'Horror',
  'https://m.media-amazon.com/images/M/MV5BYTI0ZmI4NDItZGFlZC00M2E4LWIyZWEtMTFhMjQwYmU4MGNlXkEyXkFqcGdeQXVyMTUzMTg2ODkz._V1_.jpg'],
 [2,
  2,
  'Killers of the Flower Moon',
  'https://imdb.com/title/tt5537002',
  '3h 26m',
  'https://imdb.com/video/vi784910105/?ref_=tt_vi_i_1',
  2023,
  8,
  'Crime',
  'https://m.media-amazon.com/images/M/MV5BNjQwOGM2YTItMGYwNC00YTM4LWI0Y2QtZjQ2ZDcyMmRjMTFhXkEyXkFqcGdeQXVyMDM2NDM2MQ@@._V1_.jpg'],
 [3,
  6,
  'Pain Hustlers',
  'https://imdb.com/title/tt15257160',
  '2h 2m',
  'https://imdb.com/video/vi3603023641/?ref_=tt_vi_i_1',
  2023,
  6.5,
  'Crime',
  'https://m.media-amazon.com/images/M/MV5BNWMxYjNhZmEtNDBjZi00ZjFmLWJlZDMtYTVlYjljMmNkZWFhXkEyXkFqcGdeQXVyODE5NzE3OTE@._V1_.jpg'],
 [4,
  47,
  'A Haunting in Venice',
  'https://imdb.com/title/tt22687790',
  '1h 43m',
  'https:/

In [33]:
import pandas as pd

df = pd.DataFrame(pop_movies, columns=['current ranking','previous ranking','title','link','length','trailer','year','IMDb rating','genre','poster'])
df

current ranking  previous ranking                             title  \
0                 1                 1           Five Nights at Freddy's   
1                 2                 2        Killers of the Flower Moon   
2                 3                 6                     Pain Hustlers   
3                 4                47              A Haunting in Venice   
4                 5                15                        The Killer   
..              ...               ...                               ...   
95               96                44                           Nowhere   
96               97                63  Winnie-the-Pooh: Blood and Honey   
97               98               180                         Terrifier   
98               99                90         A Nightmare on Elm Street   
99              100                89                      Doctor Sleep   

                                 link  length  \
0    https://imdb.com/title/tt4589218  1h 49m   
1    https://imdb.com/title/tt5537002  3h 26m   
2   https://imdb.com/title/tt15257160   2h 2m   
3   https://imdb.com/title/tt22687790  1h 43m   
4    https://imdb.com/title/tt1136617  1h 58m   
..                                ...     ...   
95  https://imdb.com/title/tt15789472  1h 49m   
96  https://imdb.com/title/tt19623240  1h 24m   
97   https://imdb.com/title/tt4281724  1h 25m   
98   https://imdb.com/title/tt0087800  1h 31m   
99   https://imdb.com/title/tt5606664  2h 32m   

                                              trailer  year  IMDb rating  \
0   https://imdb.com/video/vi889046809/?ref_=tt_vi...  2023          5.5   
1   https://imdb.com/video/vi784910105/?ref_=tt_vi...  2023          8.0   
2   https://imdb.com/video/vi3603023641/?ref_=tt_v...  2023          6.5   
3   https://imdb.com/video/vi1670760217/?ref_=tt_v...  2023          6.6   
4   https://imdb.com/video/vi87213849/?ref_=tt_vi_i_1  2023          7.0   
..                                                ...   ...          ...   
95  https://imdb.com/video/vi2716518169/?ref_=tt_v...  2023          6.3   
96  https://imdb.com/video/vi3211444761/?ref_=tt_v...  2023          2.9   
97  https://imdb.com/video/vi3362961433/?ref_=tt_v...  2016          5.6   
98  https://imdb.com/video/vi922076441/?ref_=tt_vi...  1984          7.4   
99  https://imdb.com/video/vi212254489/?ref_=tt_vi...  2019          7.3   

     genre                                             poster  
0   Horror  https://m.media-amazon.com/images/M/MV5BYTI0Zm...  
1    Crime  https://m.media-amazon.com/images/M/MV5BNjQwOG...  
2    Crime  https://m.media-amazon.com/images/M/MV5BNWMxYj...  
3    Crime  https://m.media-amazon.com/images/M/MV5BYmI4Mz...  
4   Action  https://m.media-amazon.com/images/M/MV5BZGJkMD...  
..     ...                                                ...  
95   Drama  https://m.media-amazon.com/images/M/MV5BNmEyOW...  
96  Horror  https://m.media-amazon.com/images/M/MV5BNGMwNj...  
97  Horror  https://m.media-amazon.com/images/M/MV5BYmMxNz...  
98  Horror  https://m.media-amazon.com/images/M/MV5BNzFjZm...  
99   Drama  https://m.media-amazon.com/images/M/MV5BMTRkYT...  

[100 rows x 10 columns]

In [34]:
# 用今天的日期來做為檔名

from datetime import datetime

date=datetime.now().strftime('%Y-%m-%d')  # m要用小寫字，因大本字是指分鐘
date

df.to_csv(f'IMDb電影排行榜_{date}.csv',encoding='utf-8-sig')